In [1]:
from tensorflow import keras
import tensorflow as tf
import os
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import seaborn as sns
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score, f1_score

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Dropout, GRU, Bidirectional, Flatten
from tensorflow.keras.optimizers import SGD
from tensorflow.random import set_seed

set_seed(2024)
np.random.seed(2024)


import csv
import librosa
import librosa.display
import matplotlib.pyplot as plt
os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"

train_dir = os.path.abspath('../data/train/train')
test_dir = os.path.abspath('../data/test/test')

classes = os.listdir(train_dir + '/audio')
# classes.remove("_background_noise_")

X_train = np.load(train_dir + "/X_train.npy")
y_train = np.load(train_dir + "/y_train.npy")

X_val = np.load(train_dir + "/X_val.npy")
y_val = np.load(train_dir + "/y_val.npy")

X_train = X_train.reshape((-1, X_train.shape[1], X_train.shape[2]))
X_val = X_val.reshape((-1, X_val.shape[1], X_val.shape[2]))

X_test = np.load(test_dir + '/X_test.npy')
X_files = np.loadtxt(test_dir + '/X_files.txt', delimiter=" ", dtype='str')

def plot_loss(history_df, name, idx):
    plt.figure()
    plt.plot(history_df['loss'])
    plt.plot(history_df['val_loss'])
    plt.title(f'{name}: loss')
    plt.ylabel('loss')
    plt.xlabel('epoch')
    plt.legend(['train', 'test'], loc='upper right')
    path = f'train_history/{name}/{idx}_loss.png'
    plt.savefig(path)
    print(f'Loss plot is saved to: {path}')
    plt.close()


In [4]:
input_shape = (122, 85)
epochs = 100
batch_size = 32


model_lstm = Sequential()
model_lstm.add(LSTM(units=125, activation="tanh", input_shape=input_shape))
model_lstm.add(Dense(units=len(classes)))
# Compiling the model
model_lstm.compile(optimizer="RMSprop", loss="mse")

print(model_lstm.summary())

# Model training
history = model_lstm.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, validation_data=(X_val, y_val))

history_df = pd.DataFrame(history.history) 
hist_csv_file = 'train_history/' + 'LSTM' + '/' + str(0) + '_history.csv'
with open(hist_csv_file, mode='w') as f:
    history_df.to_csv(f)

plot_loss(history_df, 'LSTM', str(0))

# Check validation accuracy and f1
y_pred = np.argmax(model_lstm.predict(X_val), axis=-1)
accuracy = accuracy_score(y_val, y_pred)

f1 = f1_score(y_val, y_pred, average='macro')
metrics_df = pd.DataFrame({'accuracy': [accuracy], 'f1': [f1]}) 
metrics_csv_file = 'train_history/' + 'LSTM' + '/' + str(0) + '_metrics.csv'
with open(metrics_csv_file, mode='w') as f:
    metrics_df.to_csv(f)
print(metrics_df)

# Confusion Matrix
cm = confusion_matrix(y_val, y_pred)
accuracy = accuracy_score(y_val, y_pred)
print(f'Accuracy: {accuracy * 100:.2f}%')

plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", xticklabels=range(0, 30), yticklabels=range(0, 30))
plt.xlabel('Predicted')
plt.ylabel('True')
plt.title(f'LSTM Confusion Matrix. Accuracy: {accuracy * 100:.2f}%')
path = f'train_history/LSTM/0_confusion_matrix.png'
plt.savefig(path)
print(f'Confusion matrix is saved to: {path}')
plt.close()

# Prepare submission
submission_df = pd.DataFrame({'fname': [], 'label': []}) 
for ind, test_file in enumerate(X_files):
    y_pred = np.argmax(model_lstm.predict(np.array([X_test[ind]])), axis=-1)
    submission_df.loc[len(submission_df.index)] = [X_files[ind], classes[y_pred[0]]]
submission_csv_file = 'train_history/' + 'LSTM' + '/' + str(0) + '_submission.csv'
with open(submission_csv_file, mode='w') as f:
    submission_df.to_csv(f, index=False, lineterminator='\n')
print('Submission saved.')

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_1 (LSTM)               (None, 125)               105500    
                                                                 
 dense_1 (Dense)             (None, 30)                3780      
                                                                 
Total params: 109,280
Trainable params: 109,280
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/100
1597/1597 [==============================] - 80s 49ms/step - loss: 74.5624 - val_loss: 62.1896
Epoch 2/100
1597/1597 [==============================] - 78s 49ms/step - loss: 49.7200 - val_loss: 44.3887
Epoch 3/100
1597/1597 [==============================] - 80s 50ms/step - loss: 31.4479 - val_loss: 30.6638
Epoch 4/100
1597/1597 [==============================] - 81s 51ms/step - loss: 23.2172 - val_loss: 21.4600
Epoch 5/100

MemoryError: Unable to allocate 1.63 MiB for an array with shape (2, 106512) and data type object

In [2]:
input_shape = (122, 85)
epochs = 50
batch_size = 32

model_gru = Sequential()
model_gru.add(Dropout(0.2, input_shape=input_shape))
model_gru.add(GRU(units=125, return_sequences=True))
model_gru.add(Dropout(0.2))
model_gru.add(GRU(units=125, return_sequences=True))
model_gru.add(Dropout(0.2))
model_gru.add(GRU(units=125, return_sequences=True))
model_gru.add(Dropout(0.2))
model_gru.add(Flatten()),
model_gru.add(Dense(units=125, activation="sigmoid"))
model_gru.add(Dropout(0.2))
model_gru.add(Dense(units=len(classes), activation="softmax"))
# Compiling the model
model_gru.compile(optimizer="adam", loss="mse")

print(model_gru.summary())

# Model training
history = model_gru.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, validation_data=(X_val, y_val))

history_df = pd.DataFrame(history.history) 
hist_csv_file = 'train_history/' + 'GRU' + '/' + str(1) + '_history.csv'
with open(hist_csv_file, mode='w') as f:
    history_df.to_csv(f)

plot_loss(history_df, 'GRU', str(1))

# Check validation accuracy and f1
y_pred = np.argmax(model_gru.predict(X_val), axis=-1)
accuracy = accuracy_score(y_val, y_pred)

f1 = f1_score(y_val, y_pred, average='macro')
metrics_df = pd.DataFrame({'accuracy': [accuracy], 'f1': [f1]}) 
metrics_csv_file = 'train_history/' + 'GRU' + '/' + str(1) + '_metrics.csv'
with open(metrics_csv_file, mode='w') as f:
    metrics_df.to_csv(f)
print(metrics_df)

# Confusion Matrix
cm = confusion_matrix(y_val, y_pred)
print(f'Accuracy: {accuracy * 100:.2f}%')

plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", xticklabels=range(0, 30), yticklabels=range(0, 30))
plt.xlabel('Predicted')
plt.ylabel('True')
plt.title(f'GRU Confusion Matrix. Accuracy: {accuracy * 100:.2f}%')
path = f'train_history/GRU/1_confusion_matrix.png'
plt.savefig(path)
print(f'Confusion matrix is saved to: {path}')
plt.close()

# Prepare submission
# submission_df = pd.DataFrame({'fname': [], 'label': []})
# # y_pred = np.argmax(model_gru.predict(X_test), axis=-1)
# for ind, test_file in enumerate(X_files):
#     if ind%2000 == 0:
#         print("{} done!".format(ind))
#     y_pred = np.argmax(model_gru.predict(np.array([X_test[ind]])), axis=-1)
#     submission_df.loc[len(submission_df.index)] = [X_files[ind], classes[y_pred[0]]]
# submission_csv_file = 'train_history/' + 'GRU' + '/' + str(0) + '_submission.csv'
# with open(submission_csv_file, mode='w') as f:
#     submission_df.to_csv(f, index=False, lineterminator='\n')
# print('Submission saved.')

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dropout (Dropout)           (None, 122, 85)           0         
                                                                 
 gru (GRU)                   (None, 122, 125)          79500     
                                                                 
 dropout_1 (Dropout)         (None, 122, 125)          0         
                                                                 
 gru_1 (GRU)                 (None, 122, 125)          94500     
                                                                 
 dropout_2 (Dropout)         (None, 122, 125)          0         
                                                                 
 gru_2 (GRU)                 (None, 122, 125)          94500     
                                                                 
 dropout_3 (Dropout)         (None, 122, 125)          0

# Transformer

In [4]:
from transformers import AutoFeatureExtractor, AutoModelForAudioClassification, TrainingArguments, Trainer, pipeline
import evaluate
from datasets import load_dataset, Audio

train_dir = os.path.abspath('../data/train/train')
dataset = load_dataset("audiofolder", data_dir="../data/train/train/audio")
dataset = dataset['train'].train_test_split(test_size=0.2)
labels = dataset["train"].features["label"].names
print(labels)
label2id, id2label = dict(), dict()
for i, label in enumerate(labels):
    label2id[label] = str(i)
    id2label[str(i)] = label


['bed', 'bird', 'cat', 'dog', 'down', 'eight', 'five', 'four', 'go', 'happy', 'house', 'left', 'marvin', 'nine', 'no', 'off', 'on', 'one', 'right', 'seven', 'sheila', 'six', 'stop', 'three', 'tree', 'two', 'up', 'wow', 'yes', 'zero']


In [20]:
feature_extractor = AutoFeatureExtractor.from_pretrained(
    "facebook/wav2vec2-base")

def preprocess_function(examples):
    audio_arrays = [x["array"] for x in examples["audio"]]
    inputs = feature_extractor(
      audio_arrays,
      sampling_rate=feature_extractor.sampling_rate,
      max_length=16000, truncation=True
    )
    return inputs
 
 
encoded_dataset = dataset.map(
    preprocess_function, remove_columns="audio", batched=True)
# encoded_dataset = encoded_dataset.rename_column("intent_class", "label")

encoded_dataset['train']


c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\transformers\configuration_utils.py:363: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(
Map: 100%|██████████| 12945/12945 [01:25<00:00, 150.65 examples/s]


Dataset({
    features: ['label', 'input_values'],
    num_rows: 51776
})

In [22]:


accuracy = evaluate.load("accuracy")
def compute_metrics(eval_pred):
    predictions = np.argmax(eval_pred.predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=eval_pred.label_ids)


In [23]:
import numpy as np

num_labels = len(id2label)
model = AutoModelForAudioClassification.from_pretrained(
    "facebook/wav2vec2-base", num_labels=num_labels, 
  label2id=label2id, id2label=id2label
)
 
training_args = TrainingArguments(
    output_dir="GFG_commands_audio_classification_finetuned",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    # increase this if you have better machine resources
    learning_rate=4e-4,
    # increase this if you have better machine resources
    per_device_train_batch_size=32,
    gradient_accumulation_steps=4,
    # increase this if you have better machine resources
    per_device_eval_batch_size=32,
    # increase this if you have better machine resources
    num_train_epochs=8,
    warmup_ratio=0.1,
    # increase this if you have better machine resources
    logging_steps=10,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    fp16=True,                             # set to False if you don't have GPU
)
 
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=encoded_dataset["train"].with_format("torch"),
    eval_dataset=encoded_dataset["test"].with_format("torch"),
    tokenizer=feature_extractor,
    compute_metrics=compute_metrics,
)
 
trainer.train()


c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\torch\_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
Some weights of Wav2Vec2ForSequenceClassification were not initialized from the model checkpoint at facebook/wav2vec2-base and are newly initialized: ['classifier.bias', 'classifier.weight', 'projector.bias', 'projector.weight', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
  0%|          | 10/3232 [00:07<34:06,  1.57it/s] 

{'loss': 3.3981, 'grad_norm': 0.5974945425987244, 'learning_rate': 9.876543209876543e-06, 'epoch': 0.02}


  1%|          | 20/3232 [00:12<31:08,  1.72it/s]

{'loss': 3.3927, 'grad_norm': 0.5135430097579956, 'learning_rate': 2.2222222222222223e-05, 'epoch': 0.05}


  1%|          | 30/3232 [00:18<30:46,  1.73it/s]

...

                                                   
100%|██████████| 3232/3232 [34:20<00:00,  1.67it/s]

{'eval_loss': 0.08352439105510712, 'eval_accuracy': 0.977211278485902, 'eval_runtime': 16.9383, 'eval_samples_per_second': 764.242, 'eval_steps_per_second': 23.91, 'epoch': 7.99}


100%|██████████| 3232/3232 [34:21<00:00,  1.57it/s]

{'train_runtime': 2061.452, 'train_samples_per_second': 200.93, 'train_steps_per_second': 1.568, 'train_loss': 0.5422990972379057, 'epoch': 7.99}


TrainOutput(global_step=3232, training_loss=0.5422990972379057, metrics={'train_runtime': 2061.452, 'train_samples_per_second': 200.93, 'train_steps_per_second': 1.568, 'total_flos': 3.756079796453376e+18, 'train_loss': 0.5422990972379057, 'epoch': 7.990111248454882})

In [3]:
# audio_file='../data/test/test/audio/clip_000a96d0a.wav'
import csv

classifier = pipeline("audio-classification", model="GFG_commands_audio_classification_finetuned/checkpoint-3232")

def predict(audio_file, classifier):
    prediction = classifier(audio_file)
    if len(prediction) == 0:
        print(f'no prediction for {audio_file}')
        return 'unknown'
    score = prediction[0]['score']
    if score > 0.5:
        return prediction[0]['label']
    elif score <= 0.5 and score > 0.25:
        return 'unknown'
    else:
        return 'silence'


submission_df = pd.DataFrame({'fname': [], 'label': []})
classifier = pipeline("audio-classification", model="GFG_commands_audio_classification_finetuned/checkpoint-3232")
submission_csv_file = 'GFG_commands_audio_classification_finetuned/' + 'checkpoint-3232' + '/' + str(0) + '_submission.csv'

for ind, test_file in enumerate(X_files[:4000]):
    if ind%2000 == 0:
        print("{} done!".format(ind))
    label_pred = predict(test_dir + '/audio/' + test_file, classifier)
    with open(submission_csv_file, 'a', newline='') as csvfile:
        writer = csv.writer(csvfile)
        writer.writerow([X_files[ind], label_pred])

print('Submission saved.')

0 done!
2000 done!
Submission saved.


In [53]:
classifier = pipeline("audio-classification", model="GFG_commands_audio_classification_finetuned/checkpoint-3232")

y_true = []
y_pred = []

for ind, file in enumerate(dataset['test']):
    if ind%2000 == 0:
        print("{} done!".format(ind))
    y_true.append(file['label'])
    predicted_label = predict(file['audio']['path'], classifier)
    if predicted_label in label2id:
        y_pred.append(label2id[predicted_label])
    elif predicted_label == 'unknown':
        y_pred.append(len(label2id))
    else:
        y_pred.append(len(label2id) + 1)

y_pred = [int(x) for x in y_pred]
accuracy = accuracy_score(y_true, y_pred)

# Confusion Matrix
cm = confusion_matrix(y_true, y_pred)
print(f'Accuracy: {accuracy * 100:.2f}%')

plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", xticklabels=range(0, 32), yticklabels=range(0, 32))
plt.xlabel('Predicted')
plt.ylabel('True')
plt.title(f'Transformer Confusion Matrix. Accuracy: {accuracy * 100:.2f}%')
path = f'GFG_commands_audio_classification_finetuned/checkpoint-3232/0_confusion_matrix.png'
plt.savefig(path)
print(f'Confusion matrix is saved to: {path}')
plt.close()

0 done!
2000 done!
4000 done!
6000 done!
8000 done!
10000 done!
12000 done!
Accuracy: 97.95%
Confusion matrix is saved to: GFG_commands_audio_classification_finetuned/checkpoint-3232/0_confusion_matrix.png
